In [1]:
import pandas as pd
from ast import literal_eval
import numpy as np
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
from statistics import mean, median
import scipy
from sklearn.decomposition import PCA
from sklearn import preprocessing
from gprofiler import GProfiler
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
figure(num=None, figsize=(8, 6), dpi=80, facecolor='w', edgecolor='k')
import operator
import qvalue as qv


#Reactome file containing information on pathways, the genes they contain and pathway name, also including the illumina identifier for the genes.

reactome = pd.read_csv('../data/reactome.csv', sep=',', index_col = 0)

def read_reactome(file_name, gene_name_start = "ENSG0"):
    df = pd.read_csv(file_name, sep='\t', header=None)
    
    if gene_name_start == None:
        sub_df = df
    else:
        subset_vec = df[0].str.startswith(gene_name_start)
        sub_df = df.loc[subset_vec]
    
    genes_df = sub_df.groupby(1)[0].apply(list)
    names_df = sub_df.groupby(1)[3].max()
    
    out_df = pd.concat([genes_df,names_df], axis=1)
    out_df.columns = ['genes', 'pathway_name']
    
    return out_df

low_level = read_reactome('../data/Ensembl2Reactome_All_Levels.txt.gz')

def my_pca(df, n_pc=1, normalize=True):
    df = df.dropna(axis = 0, how = 'all')#redundant, but keeping it just in case
    X = df.values.T
    if normalize:
        X2 = preprocessing.scale(X)
    else:
        X2 = X
    pca = PCA(n_components = n_pc)
    pca.fit(X2)
    my_pca.pca = pca  #needed for components
    Xnew = pca.fit_transform(X2)
    out_df = pd.DataFrame(Xnew.transpose(), index=list(range(1,n_pc+1)), columns=df.columns)
    out_df = out_df.transpose()
    
    return out_df, my_pca.pca.components_, my_pca.pca.explained_variance_ratio_

#Importing metabric dataset, dividing up what is clinical/expression data and changing the type of the expression columns to float
metabric_data = pd.read_csv('../data/metabric.csv.gz')
#clinical_data = metabric_data.iloc[:27, :]
expression_data = metabric_data.iloc[27:,:]

#print(expression_data.columns)
dtypedict = {}
for i in expression_data.columns[1:]:
    dtypedict[i] = 'float32'
expression_data = expression_data.astype(dtypedict)



new_clinical_patient = pd.read_csv('../data/data_clinical_patient.txt', sep='\t', index_col=0).iloc[4:]
new_clinical_sample = pd.read_csv('../data/data_clinical_sample.txt', sep='\t', index_col=0).iloc[4:]
new_clinical = pd.concat([new_clinical_patient, new_clinical_sample.reindex(new_clinical_patient.index)], axis=1)
new_clinical['Triple Neg'] = new_clinical.apply(lambda row: True if ((row['ER Status'] == 'Negative') 
                                                                     and (row['PR Status'] == 'Negative') 
                                                                     and (row['HER2 Status'] == 'Negative')) else False, axis = 1)

new_clinical['ER-/PR-/HER2+'] = new_clinical.apply(lambda row: True if ((row['ER Status'] == 'Negative') 
                                                                     and (row['PR Status'] == 'Negative') 
                                                                     and (row['HER2 Status'] == 'Positive')) else False, axis = 1)





genes = expression_data['Unnamed: 0'].values.tolist()

gp = GProfiler(return_dataframe = True)
gp = gp.convert(organism='hsapiens',
          query=genes)

gp = gp.loc[gp['n_converted'] == 1]
gp = gp.loc[gp['name'] != 'None']
gp = gp.set_index('incoming')
gprofiler_names = gp
gprofiler_names

dataset = expression_data.set_index('Unnamed: 0') #gene_patient
pca_per_pathway = pd.DataFrame(index=expression_data.columns)

real_gene_names = pd.read_csv('../data/illumina2symbol.txt', sep="\t", index_col = 0)


In [2]:
genes_components_per_pathway = {} #nested dictionary where the 'outer dictionary' is the pathway names as keys and values are 
                                  #another dictionary with genes as keys and components as values

for pathway in reactome.index:
    genes = reactome.loc[pathway, "illumina"]
    genes = literal_eval(genes)
    genes = list(filter(lambda a: a != 'NaN', genes))
    pathwaydata = dataset.loc[genes]
    if pathwaydata.index.empty == True:
        pass
    else:
        pathwaydata = pathwaydata.dropna(axis = 0, how = 'any') #has to be done so the lists match, this makes the dropna in my_pca function obsolete
        presentgenes = pathwaydata.index.values.tolist()
        if len(presentgenes) <= 1:
            pass
        else:
            res, components, explained_variance = my_pca(pathwaydata)
            print(res)
            pathwayname = reactome.loc[pathway, 'pathway_name']
            pca_per_pathway[pathwayname] = res

            components = components.tolist()[0]
            innerdict = {}
            for i in range(0, len(presentgenes)):
                component = components[i]
                gene = genes[i]
                if gene in real_gene_names.index:
                    real_name = real_gene_names.loc[gene, "symbol"]
                    innerdict[real_name] = component
                elif gene in gprofiler_names.index:
                    real_name = gprofiler_names.loc[gene, 'name']
                    innerdict[real_name] = component
                else:
                    innerdict[gene] = component
            sorted_innerdict = sorted(innerdict.items(), key = operator.itemgetter(1), reverse = True)
            genes_components_per_pathway[pathwayname] = [sorted_innerdict, explained_variance.flat[0]]

pca_per_pathway = pca_per_pathway.iloc[1:]

                1
MB-0002 -0.464918
MB-0008  1.135675
MB-0010 -0.016409
MB-0035 -0.045985
MB-0036 -1.107914
MB-0050  1.003815
MB-0059 -0.473152
MB-0060  0.681488
MB-0066  0.539737
MB-0101  1.391562
MB-0102  0.975993
MB-0106 -1.716131
MB-0112  0.721623
MB-0115  2.891249
MB-0117 -1.218243
MB-0119  0.324921
MB-0120 -1.282450
MB-0121  0.066521
MB-0122  0.241642
MB-0123  0.632201
MB-0126  0.430238
MB-0131  0.059168
MB-0133 -0.570784
MB-0135 -0.117804
MB-0136  0.874497
MB-0138  1.158645
MB-0139  2.100201
MB-0140 -0.166484
MB-0142 -0.881737
MB-0143  0.237472
...           ...
MB-7264  0.052618
MB-7266 -2.427948
MB-7267  1.027192
MB-7268  0.899952
MB-7269 -1.542245
MB-7270 -0.818141
MB-7273  0.133796
MB-7275  0.119506
MB-7276  1.452775
MB-7277 -0.836271
MB-7278 -0.750753
MB-7279 -0.591864
MB-7280  3.168234
MB-7281 -0.708821
MB-7283 -1.524784
MB-7284 -1.585523
MB-7285  2.112236
MB-7286  0.464737
MB-7287 -0.461483
MB-7288  0.084161
MB-7289  0.948160
MB-7291  1.676026
MB-7292 -0.991138
MB-7293  0

                1
MB-0002  4.655568
MB-0008  8.272937
MB-0010  5.898238
MB-0035  0.494913
MB-0036  4.147962
MB-0050 -1.933749
MB-0059  0.905942
MB-0060 -1.130984
MB-0066 -1.228741
MB-0101  6.086671
MB-0102  3.120502
MB-0106  2.340539
MB-0112  6.462939
MB-0115  3.692866
MB-0117 -0.745161
MB-0119  7.126933
MB-0120  8.332043
MB-0121  1.312075
MB-0122  1.857699
MB-0123  6.007670
MB-0126  6.382888
MB-0131  1.849582
MB-0133 -3.666936
MB-0135  0.420730
MB-0136 -4.222498
MB-0138  1.301518
MB-0139 -2.491192
MB-0140  2.869866
MB-0142  4.153456
MB-0143  1.076458
...           ...
MB-7264  3.076340
MB-7266  7.640169
MB-7267  4.764863
MB-7268  0.048722
MB-7269  2.775679
MB-7270  9.691806
MB-7273 -0.342196
MB-7275  0.164049
MB-7276 -2.698675
MB-7277 -1.550794
MB-7278  0.962199
MB-7279 -2.671317
MB-7280  3.281407
MB-7281 -1.002800
MB-7283 -2.440549
MB-7284 -3.839312
MB-7285  4.370538
MB-7286 -2.683914
MB-7287  2.022613
MB-7288  3.261115
MB-7289 -0.795145
MB-7291 -1.753836
MB-7292  6.284087
MB-7293 -1

                1
MB-0002 -0.914641
MB-0008  0.457897
MB-0010 -2.114127
MB-0035  0.535430
MB-0036 -0.270441
MB-0050  1.957524
MB-0059 -0.177012
MB-0060  0.233747
MB-0066 -1.427829
MB-0101 -0.919564
MB-0102 -0.418380
MB-0106  0.001738
MB-0112 -0.955716
MB-0115  2.179708
MB-0117  0.752167
MB-0119  0.309472
MB-0120 -1.337440
MB-0121  0.576467
MB-0122 -0.080777
MB-0123 -0.468607
MB-0126 -0.151945
MB-0131  0.592908
MB-0133  0.309529
MB-0135 -0.146900
MB-0136 -1.174273
MB-0138 -0.209947
MB-0139  0.100593
MB-0140  0.920864
MB-0142 -2.338976
MB-0143 -0.386166
...           ...
MB-7264 -1.394789
MB-7266 -0.134908
MB-7267  1.489457
MB-7268  0.485103
MB-7269 -0.560243
MB-7270  3.984456
MB-7273  1.437956
MB-7275  0.154371
MB-7276  0.761561
MB-7277  0.264397
MB-7278 -0.775759
MB-7279 -0.367922
MB-7280 -1.047811
MB-7281 -0.417033
MB-7283 -0.578974
MB-7284  0.224464
MB-7285  0.265898
MB-7286  0.849218
MB-7287  2.224647
MB-7288  0.046343
MB-7289  0.093806
MB-7291  0.578138
MB-7292 -1.204709
MB-7293 -1

                1
MB-0002  0.911132
MB-0008 -0.274560
MB-0010 -0.486495
MB-0035  1.666544
MB-0036  0.454604
MB-0050 -2.631706
MB-0059  0.498234
MB-0060  0.863787
MB-0066 -0.298690
MB-0101 -0.948467
MB-0102 -0.973039
MB-0106  0.088843
MB-0112 -2.478520
MB-0115 -2.419765
MB-0117 -0.014375
MB-0119  0.321108
MB-0120 -0.354665
MB-0121 -2.073057
MB-0122 -0.940425
MB-0123 -3.376526
MB-0126 -1.089332
MB-0131 -1.178035
MB-0133 -0.988906
MB-0135  0.039807
MB-0136 -2.436275
MB-0138 -0.284527
MB-0139 -2.429253
MB-0140 -1.366026
MB-0142  0.701772
MB-0143  0.308349
...           ...
MB-7264 -0.161222
MB-7266  2.927498
MB-7267  0.048690
MB-7268  0.227494
MB-7269  0.073937
MB-7270  0.871249
MB-7273 -0.918183
MB-7275 -3.327753
MB-7276  1.933629
MB-7277 -1.132364
MB-7278  0.612618
MB-7279  3.943243
MB-7280  0.053590
MB-7281  0.453726
MB-7283  3.615054
MB-7284 -0.490245
MB-7285 -3.365469
MB-7286 -0.991041
MB-7287 -0.828698
MB-7288 -2.184088
MB-7289 -3.948154
MB-7291 -5.250154
MB-7292 -1.007860
MB-7293 -3

                1
MB-0002 -0.806951
MB-0008 -0.257332
MB-0010 -0.360987
MB-0035 -2.136933
MB-0036 -0.325343
MB-0050 -1.070940
MB-0059 -1.313803
MB-0060  0.548853
MB-0066 -0.768424
MB-0101 -0.563554
MB-0102 -0.555385
MB-0106  0.182000
MB-0112 -1.372653
MB-0115  2.613843
MB-0117 -1.116497
MB-0119 -1.354585
MB-0120  0.622492
MB-0121 -0.061743
MB-0122 -0.502439
MB-0123 -0.933893
MB-0126 -0.796146
MB-0131 -0.326958
MB-0133 -0.283277
MB-0135 -0.371664
MB-0136 -0.540872
MB-0138 -1.529770
MB-0139 -0.861954
MB-0140  0.688246
MB-0142  0.043591
MB-0143  1.080839
...           ...
MB-7264 -1.154892
MB-7266 -0.080494
MB-7267  0.145592
MB-7268 -1.172301
MB-7269 -0.296235
MB-7270  0.437108
MB-7273 -1.208908
MB-7275 -0.090044
MB-7276 -1.668116
MB-7277  1.286523
MB-7278 -0.867535
MB-7279  0.074115
MB-7280 -0.776991
MB-7281  1.140578
MB-7283  0.985951
MB-7284 -1.381073
MB-7285 -1.203246
MB-7286 -0.447265
MB-7287  0.384839
MB-7288 -1.459162
MB-7289 -1.535503
MB-7291 -0.716922
MB-7292  0.513459
MB-7293 -0

...

                1
MB-0002  1.570634
MB-0008 -0.658396
MB-0010 -0.288837
MB-0035 -3.620333
MB-0036 -1.095644
MB-0050  1.308749
MB-0059 -1.681217
MB-0060 -5.850126
MB-0066 -2.088755
MB-0101 -0.353912
MB-0102  0.946636
MB-0106  2.981141
MB-0112 -2.895616
MB-0115 -3.612992
MB-0117  2.649334
MB-0119 -0.660316
MB-0120 -0.242989
MB-0121 -1.048803
MB-0122 -0.633354
MB-0123 -1.546673
MB-0126  0.747619
MB-0131 -0.586726
MB-0133  0.995054
MB-0135 -0.673380
MB-0136  1.036878
MB-0138  1.098966
MB-0139  1.645212
MB-0140 -1.347413
MB-0142 -0.805879
MB-0143 -3.517093
...           ...
MB-7264  1.739604
MB-7266 -0.591069
MB-7267 -2.374400
MB-7268 -0.977197
MB-7269 -1.151427
MB-7270  1.806199
MB-7273 -2.950928
MB-7275 -0.899311
MB-7276  1.607472
MB-7277  1.704280
MB-7278  0.628136
MB-7279 -0.017925
MB-7280  2.044104
MB-7281 -0.567333
MB-7283 -1.483843
MB-7284  0.165127
MB-7285  0.381534
MB-7286  0.462794
MB-7287 -3.602084
MB-7288 -2.045181
MB-7289  1.332030
MB-7291 -2.260669
MB-7292 -3.785775
MB-7293  1

                1
MB-0002  0.739289
MB-0008  0.988857
MB-0010 -0.190095
MB-0035 -0.433965
MB-0036 -1.096966
MB-0050 -1.846095
MB-0059 -0.815685
MB-0060  2.407383
MB-0066 -1.663843
MB-0101 -1.649601
MB-0102  0.029005
MB-0106 -0.685774
MB-0112 -0.638094
MB-0115  1.927094
MB-0117 -1.933538
MB-0119  1.341050
MB-0120  0.555937
MB-0121 -1.003161
MB-0122 -1.803253
MB-0123  0.087412
MB-0126 -1.354507
MB-0131 -2.157405
MB-0133 -3.425507
MB-0135 -0.551343
MB-0136 -1.491377
MB-0138 -1.701055
MB-0139 -2.825642
MB-0140 -1.481639
MB-0142 -1.266918
MB-0143  0.468472
...           ...
MB-7264  0.074168
MB-7266  0.038547
MB-7267  2.919846
MB-7268 -0.080610
MB-7269  4.421101
MB-7270  0.724511
MB-7273  1.814047
MB-7275 -0.161314
MB-7276 -2.164045
MB-7277 -1.464962
MB-7278 -0.816835
MB-7279  4.257286
MB-7280  0.466759
MB-7281  2.228114
MB-7283  0.193123
MB-7284  0.054875
MB-7285 -0.440997
MB-7286 -2.713407
MB-7287  0.643572
MB-7288 -1.699996
MB-7289 -1.742276
MB-7291  0.006406
MB-7292  1.159750
MB-7293 -1

                1
MB-0002 -0.066749
MB-0008 -0.707655
MB-0010  0.981741
MB-0035  0.563124
MB-0036  0.056668
MB-0050 -0.368493
MB-0059 -0.372931
MB-0060 -0.394455
MB-0066  0.502120
MB-0101 -1.026724
MB-0102 -0.734611
MB-0106  0.472311
MB-0112 -1.370069
MB-0115 -0.905844
MB-0117 -0.121077
MB-0119 -0.416084
MB-0120 -0.366522
MB-0121  0.189822
MB-0122  0.160487
MB-0123  0.574068
MB-0126 -0.793298
MB-0131  0.148435
MB-0133 -4.457086
MB-0135 -0.802384
MB-0136 -0.936826
MB-0138 -1.160225
MB-0139 -1.472890
MB-0140  0.347901
MB-0142  0.552486
MB-0143  0.205637
...           ...
MB-7264 -0.675160
MB-7266  1.964212
MB-7267 -0.291931
MB-7268  0.738586
MB-7269  2.390436
MB-7270  3.287607
MB-7273 -0.159837
MB-7275 -0.368931
MB-7276 -0.183985
MB-7277  0.650012
MB-7278  0.947675
MB-7279 -1.548732
MB-7280  0.587725
MB-7281  0.323012
MB-7283  0.180580
MB-7284 -0.428158
MB-7285  0.762981
MB-7286 -0.838388
MB-7287 -1.477247
MB-7288  0.588075
MB-7289 -2.679454
MB-7291  0.187250
MB-7292 -0.875250
MB-7293 -0

                1
MB-0002  1.678981
MB-0008 -1.952099
MB-0010 -0.581950
MB-0035  0.869068
MB-0036 -0.443175
MB-0050 -1.547304
MB-0059 -0.084519
MB-0060 -2.902006
MB-0066  0.364965
MB-0101 -0.412586
MB-0102 -1.043224
MB-0106 -1.624027
MB-0112  0.222504
MB-0115  1.292151
MB-0117 -0.530494
MB-0119  1.644231
MB-0120 -0.238766
MB-0121 -0.250309
MB-0122 -1.872214
MB-0123 -2.108211
MB-0126 -1.451660
MB-0131  0.331635
MB-0133 -0.232068
MB-0135 -1.554599
MB-0136 -1.897205
MB-0138 -0.705117
MB-0139 -1.488985
MB-0140 -2.082912
MB-0142  0.348865
MB-0143  1.056987
...           ...
MB-7264 -1.010778
MB-7266 -1.566660
MB-7267  2.719343
MB-7268 -0.722425
MB-7269  0.832176
MB-7270  0.524581
MB-7273  1.209914
MB-7275 -1.535200
MB-7276 -1.995799
MB-7277  0.958728
MB-7278 -2.766442
MB-7279  0.592211
MB-7280  1.012720
MB-7281 -0.905139
MB-7283  0.484754
MB-7284 -0.732662
MB-7285 -2.032617
MB-7286 -0.875719
MB-7287  0.558738
MB-7288 -1.604715
MB-7289 -2.558696
MB-7291 -1.033376
MB-7292 -1.769590
MB-7293 -0

                 1
MB-0002  -0.181216
MB-0008  -6.103697
MB-0010  -4.429465
MB-0035   2.307193
MB-0036   0.652170
MB-0050  -1.234761
MB-0059  -4.292349
MB-0060  -7.273606
MB-0066  -7.044342
MB-0101  -1.349729
MB-0102  -3.961121
MB-0106   2.509519
MB-0112  -3.463128
MB-0115  -5.246091
MB-0117   0.818819
MB-0119  -2.911417
MB-0120  -1.535760
MB-0121  -6.407048
MB-0122  -4.043545
MB-0123  -9.242506
MB-0126  -0.852173
MB-0131  -1.802840
MB-0133   2.981792
MB-0135  -3.796860
MB-0136  -5.329273
MB-0138   2.631021
MB-0139  -0.110126
MB-0140  -1.463622
MB-0142   1.139715
MB-0143  -1.103451
...            ...
MB-7264   2.978945
MB-7266   0.236278
MB-7267   1.234858
MB-7268  -2.645633
MB-7269  -2.246195
MB-7270   0.104628
MB-7273  -6.583871
MB-7275  -6.027483
MB-7276  -0.924464
MB-7277  -2.903464
MB-7278   2.780077
MB-7279   7.453164
MB-7280   0.306341
MB-7281   0.093177
MB-7283   5.662930
MB-7284  -0.075529
MB-7285  -5.234863
MB-7286  -2.372414
MB-7287  -7.005778
MB-7288  -9.528713
MB-7289  -5.

In [3]:
full_df = pd.concat([pca_per_pathway, new_clinical.reindex(pca_per_pathway.index)], axis= 1)

In [4]:
from scipy.stats import ttest_ind, mannwhitneyu
import qvalue as qv

clusterframes = {}

grouped_by_cluster = full_df.groupby('Integrative Cluster')

for group in grouped_by_cluster:
    df_cluster = pd.DataFrame(index=full_df.iloc[:,:-33].columns)
    groupname = group[0]
    df = group[1].iloc[:,:-33]
    group2_df = full_df[full_df['Integrative Cluster'] != groupname].iloc[:,:-33]
    pvaluelist = []
    group1_mean_list = []
    group2_mean_list = []
    for pathway in df:
        group = df[pathway]
        group2 = group2_df[pathway]
        test = mannwhitneyu(group, group2)
        pvaluelist.append(test[1])
        group_mean = group.mean()
        group1_mean_list.append(group_mean)
        group2_mean = group2.mean()
        group2_mean_list.append(group2_mean) 
        
    
    df_cluster[f'Cluster {groupname}'] = group1_mean_list
    df_cluster['Other clusters'] = group2_mean_list
    df_cluster['Fold Change'] = np.log2(abs(df_cluster[f'Cluster {groupname}'])) - np.log2(abs(df_cluster['Other clusters']))
    
    
    df_cluster['p-values'] = pvaluelist
    qv.qvalues(df_cluster, 'p-values', f'cluster {groupname} qvalues')
    df_cluster['p-values'] = -np.log10(df_cluster['p-values'])
    df_cluster[f'cluster {groupname} qvalues'] = -np.log10(df_cluster[f'cluster {groupname} qvalues'])
    print(groupname)
    clusterframes[groupname] = df_cluster
        
        
clusterframes

1
10
2
3
4ER+
4ER-
5
6
7
8
9


{'1':                                                     Cluster 1  Other clusters  \
 Chromosome Maintenance                               4.327114       -0.324592   
 RMTs methylate histone arginines                     4.292748       -0.322014   
 Cellular Senescence                                  4.878702       -0.365969   
 Nucleosome assembly                                  4.022460       -0.301738   
 Deposition of new CENPA-containing nucleosomes ...   4.022460       -0.301738   
 HDMs demethylate histones                            3.059041       -0.229469   
 Senescence-Associated Secretory Phenotype (SASP)     4.524311       -0.339384   
 Telomere Maintenance                                 3.916533       -0.293793   
 Estrogen-dependent gene expression                   4.535727       -0.340241   
 Oxidative Stress Induced Senescence                  4.423600       -0.331830   
 Meiosis                                              4.409991       -0.330809   
 Reproducti

In [5]:
gene_expression_per_pathway = pd.DataFrame(index=expression_data.columns)
for pathway in reactome.index:
    genes = reactome.loc[pathway, "illumina"]
    genes = literal_eval(genes)
    genes = list(filter(lambda a: a != 'NaN', genes))
    pathwaydata = dataset.loc[genes]
    pathwaydata = pathwaydata.dropna(axis = 0, how = 'any') #has to be done so the lists match, this makes the dropna in my_pca function obsolete
    presentgenes = pathwaydata.index.values.tolist()
    if len(presentgenes) <= 1:
        pass
    else:
        X = pathwaydata.values.T
        X2 = preprocessing.scale(X)
        pathwayname = reactome.loc[pathway, 'pathway_name']
        out_df = pd.DataFrame(X2, columns = presentgenes, index = dataset.columns)
        gene_expression_series = out_df.mean(axis=1)
        gene_expression_per_pathway[pathwayname] = gene_expression_series
        
gene_expression_per_pathway = gene_expression_per_pathway[1:]

In [6]:
full_GE_df = pd.concat([gene_expression_per_pathway, new_clinical.reindex(gene_expression_per_pathway.index)], axis=1)

In [7]:
from scipy.stats import ttest_ind, mannwhitneyu
import qvalue as qv

clusterframes_GE = {}

grouped_by_cluster = full_GE_df.groupby('Integrative Cluster')

for group in grouped_by_cluster:
    df_cluster = pd.DataFrame(index=full_GE_df.iloc[:,:-33].columns)
    groupname = group[0]
    df = group[1].iloc[:,:-33]
    group2_df = full_GE_df[full_GE_df['Integrative Cluster'] != groupname].iloc[:,:-33]
    pvaluelist = []
    group1_mean_list = []
    group2_mean_list = []
    for pathway in df:
        group = df[pathway]
        group2 = group2_df[pathway]
        test = mannwhitneyu(group, group2)
        pvaluelist.append(test[1])
        group_mean = group.mean()
        group1_mean_list.append(group_mean)
        group2_mean = group2.mean()
        group2_mean_list.append(group2_mean) 
        
    
    df_cluster[f'Cluster {groupname}'] = group1_mean_list
    df_cluster['Other clusters'] = group2_mean_list
    df_cluster['Fold Change'] = np.log2(abs(df_cluster[f'Cluster {groupname}'])) - np.log2(abs(df_cluster['Other clusters']))
    
    
    df_cluster['p-values'] = pvaluelist
    qv.qvalues(df_cluster, 'p-values', f'cluster {groupname} qvalues')
    df_cluster['p-values'] = -np.log10(df_cluster['p-values'])
    df_cluster[f'cluster {groupname} qvalues'] = -np.log10(df_cluster[f'cluster {groupname} qvalues'])
    print(groupname)
    clusterframes_GE[groupname] = df_cluster
        
        
clusterframes_GE

1
10
2
3
4ER+
4ER-
5
6
7
8
9


{'1':                                                     Cluster 1  Other clusters  \
 Base Excision Repair                                 0.341325       -0.025604   
 Estrogen-dependent gene expression                   0.269920       -0.020248   
 Chromosome Maintenance                               0.366366       -0.027482   
 Telomere Maintenance                                 0.380798       -0.028565   
 RMTs methylate histone arginines                     0.370195       -0.027770   
 Nucleosome assembly                                  0.419918       -0.031500   
 Deposition of new CENPA-containing nucleosomes ...   0.419918       -0.031500   
 HCMV Late Events                                     0.343341       -0.025755   
 Meiotic recombination                                0.371719       -0.027884   
 Transcriptional regulation by small RNAs             0.349776       -0.026238   
 Meiosis                                              0.297699       -0.022331   
 ESR-mediat

In [8]:
for i in clusterframes:
    print(clusterframes[i][f'cluster {i} qvalues'])
    print('')

Chromosome Maintenance                                                                                                        28.690694
RMTs methylate histone arginines                                                                                              27.805190
Cellular Senescence                                                                                                           27.248127
Nucleosome assembly                                                                                                           27.248127
Deposition of new CENPA-containing nucleosomes at the centromere                                                              27.248127
HDMs demethylate histones                                                                                                     26.953585
Senescence-Associated Secretory Phenotype (SASP)                                                                              26.833820
Telomere Maintenance                            

In [9]:
for i in clusterframes_GE:
    print(clusterframes_GE[i][f'cluster {i} qvalues'])
    print('')

Base Excision Repair                                                                          31.002611
Estrogen-dependent gene expression                                                            31.002611
Chromosome Maintenance                                                                        31.002611
Telomere Maintenance                                                                          30.984180
RMTs methylate histone arginines                                                              30.984180
Nucleosome assembly                                                                           30.984180
Deposition of new CENPA-containing nucleosomes at the centromere                              30.984180
HCMV Late Events                                                                              30.893911
Meiotic recombination                                                                         29.925452
Transcriptional regulation by small RNAs                        

In [10]:
gsea_test_df = pd.concat([clusterframes['1']['cluster 1 qvalues'], clusterframes_GE['1']['cluster 1 qvalues']], axis=1)
gsea_test_df.columns = ['PCA', 'GE'] 
gsea_test_df['C'] = np.arange(len(gsea_test_df))
gsea_test_df

PCA         GE     C
2-LTR circle formation                               3.335132   4.393871     0
5-Phosphoribose 1-diphosphate biosynthesis           0.333542   0.365868     1
A tetrasaccharide linker sequence is required f...   7.579423   3.101784     2
ABC transporter disorders                            6.786122  11.377173     3
ABC transporters in lipid homeostasis                1.899576   3.551527     4
ABC-family proteins mediated transport               6.531222  12.092972     5
ABO blood group biosynthesis                         0.701136   0.714475     6
ADP signalling through P2Y purinoceptor 1            1.422883   0.433506     7
ADP signalling through P2Y purinoceptor 12           2.737575   0.739774     8
AKT phosphorylates targets in the cytosol            2.827611   0.952043     9
AKT phosphorylates targets in the nucleus            7.114942   2.620374    10
AKT-mediated inactivation of FOXO1A                  4.822751   3.803293    11
ALKBH3 mediated reversal of alkylation damage        0.478625   2.794560    12
AMER1 mutants destabilize the destruction complex    0.794994   0.346056    13
AMPK inhibits chREBP transcriptional activation...   7.578484   1.347575    14
APC truncation mutants have impaired AXIN binding    0.794994   0.346056    15
APC-Cdc20 mediated degradation of Nek2A             20.472928  10.694346    16
APC/C-mediated degradation of cell cycle proteins   11.885203  15.400624    17
APC/C:Cdc20 mediated degradation of Cyclin B        20.563388   9.864619    18
APC/C:Cdc20 mediated degradation of Securin          7.596092  12.295284    19
APC/C:Cdc20 mediated degradation of mitotic pro...   9.920615  13.653838    20
APC/C:Cdh1 mediated degradation of Cdc20 and ot...   8.808194  13.623056    21
APC:Cdc20 mediated degradation of cell cycle pr...   8.975483  13.093345    22
APEX1-Independent Resolution of AP Sites via th...   0.719067   0.413394    23
APOBEC3G mediated resistance to HIV-1 infection      5.781708   7.554342    24
ARL13B-mediated ciliary trafficking of INPP5E        0.673126   0.617829    25
ARMS-mediated activation                             5.523447   0.646480    26
ATF4 activates genes in response to endoplasmic...   2.559906   5.002026    27
ATF6 (ATF6-alpha) activates chaperone genes          0.401839   0.656878    28
ATF6 (ATF6-alpha) activates chaperones               0.370996   2.097354    29
...                                                       ...        ...   ...
mitochondrial fatty acid beta-oxidation of satu...   0.637301   2.912110  2044
mitochondrial fatty acid beta-oxidation of unsa...   1.392373   4.397366  2045
p130Cas linkage to MAPK signaling for integrins      2.257763   0.933441  2046
p38MAPK events                                       0.411842   0.971699  2047
p53-Dependent G1 DNA Damage Response                 6.473087  11.609761  2048
p53-Dependent G1/S DNA damage checkpoint             6.473087  11.609761  2049
p53-Independent DNA Damage Response                  6.031313  10.070761  2050
p53-Independent G1/S DNA damage checkpoint           6.031313  10.070761  2051
p75 NTR receptor-mediated signalling                 8.848270   0.689204  2052
p75NTR negatively regulates cell cycle via SC1       3.402176   0.495781  2053
p75NTR recruits signalling complexes                 2.016638   1.090523  2054
p75NTR regulates axonogenesis                        1.062906   1.888341  2055
p75NTR signals via NF-kB                             3.982775   0.370683  2056
phospho-PLA2 pathway                                 1.256684   2.158007  2057
phosphorylation site mutants of CTNNB1 are not ...   1.232780   0.477228  2058
rRNA modification in the mitochondrion               2.062072   1.394228  2059
rRNA modification in the nucleus and cytosol         2.121838   3.116575  2060
rRNA processing                                      0.337326   3.003287  2061
rRNA processing in the mitochondrion                 2.231357   4.872871  2062
rRNA processing in the nucleu

In [11]:
names = gp.get_library_name(database='Human')
print(names)

AttributeError: 'DataFrame' object has no attribute 'get_library_name'

In [22]:
clusters = new_clinical["Integrative Cluster"].unique().tolist()
for i in clusters:
    if type(i) == str:
        print(i)
    

4ER+
3
9
7
4ER-
5
8
10
1
2
6


In [ ]:
expression_data.index = expression_data['Unnamed: 0']
expression_data = expression_data.iloc[:,1:]
expression_data = expression_data.rename(index= lambda x: gprofiler_names.loc[x, 'name'] if x in gprofiler_names.index else x)
expression_data = expression_data.rename(index= lambda x: real_gene_names.loc[x, 'symbol'] if x in real_gene_names.index else x)

expression_data

In [ ]:
import gseapy as gp
gseapatients = expression_data.columns.tolist()
new_clinical_patients = new_clinical.loc[gseapatients]
classes = ['cluster 1' if patient == '1' else 'not' for patient in new_clinical_patients['Integrative Cluster']]
classes2 = [x for x in new_clinical_patients['Integrative Cluster']]


gs_res = gp.gsea(data = expression_data, 
                 gene_sets ='Reactome_2016',
                 method = "t_test",
                 permutation_num = 10,
                 processes = 4,
                 cls = classes2)

In [ ]:
gs_res.res2d.head()

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
for i in clusterframes:
    
    PCA_array = clusterframes[i][f'cluster {i} qvalues']
    GE_array = clusterframes_GE[i][f'cluster {i} qvalues']
    df = pd.concat([PCA_array, GE_array], axis=1)
    df.columns = ['PCA', 'GE']
    similarity = cosine_similarity(df.PCA.values.reshape(1, -1), df.GE.values.reshape(1, -1))
    print(similarity[0][0])